# Process function

In [1]:
%run Mylib_import.ipynb
exp_dir = "Arisa_NNSIFT"
create_folder(exp_dir)

def process_point_clouds(src, tar):   
    check_cl_src = check_pc_has_color(src)
    check_cl_tar = check_pc_has_color(tar)

    def compute_transformation_using_fpfh():
        # Compute FPFH features
        source_fpfh = compute_fpfh_features(src)
        target_fpfh = compute_fpfh_features(tar)

        # Match the features
        matches = o3d.registration.registration_ransac_based_on_feature_matching(
            src, tar, source_fpfh, target_fpfh,
            max_correspondence_distance=0.1,
            estimation_method=o3d.registration.TransformationEstimationPointToPoint(False),
            ransac_n=4,
            checkers=[o3d.registration.CorrespondenceCheckerBasedOnEdgeLength(0.9),
                      o3d.registration.CorrespondenceCheckerBasedOnDistance(0.1)],
            criteria=o3d.registration.RANSACConvergenceCriteria(4000000, 500)
        )

        return matches.transformation, 0

    if check_cl_src == 'No' or check_cl_tar == 'No':
        print("----- Non-colored point clouds ------")
        transformation, if_col = compute_transformation_using_fpfh()
        imdim = 0
        keypoints = [0, 0]
        
    else:
        print("----- Colored point clouds ------")
        # calculates img_dim referring pointclouds sizes
        imdim = 50
        
        # Generate pseudo-images (color maps) for both point clouds:    
        src_colormap, src_pointmap = point_cloud_to_color_and_point_map(src, img_dim=imdim)
        tar_colormap, tar_pointmap  = point_cloud_to_color_and_point_map(tar, img_dim=imdim)

        # Extracting SIFT keypoints and descriptors: from the pseudo-images.   
        src_keypoints, src_descriptors = extract_sift_feat(src_colormap)
        tar_keypoints, tar_descriptors = extract_sift_feat(tar_colormap)
        print(f"Number of source keypoints extracted: {len(src_keypoints), len(tar_keypoints)}")
        #draw_keypoints(src_colormap, src_keypoints, 'Source pseudo-image Keypoints')
        #draw_keypoints(tar_colormap, tar_keypoints, 'Target pseudo-image Keypoints')
        #cv2.waitKey(0)
        #cv2.destroyAllWindows()
        
        if len(src_keypoints) <= 2 or len(tar_keypoints) <= 2:
            print("----- Keypoints are not proper detected ------")
            transformation, if_col = compute_transformation_using_fpfh()
            keypoints = [len(src_keypoints), len(tar_keypoints)]
        else:
            if_col = 1
            # Project the keypoints from 2D to 3D using the point map
            src_keypoints_3d, src_pseudesc = project_keypoints_to_3D(src_keypoints, src_descriptors, src_pointmap)
            tar_keypoints_3d, tar_pseudesc = project_keypoints_to_3D(tar_keypoints, tar_descriptors, tar_pointmap)

            # Debugging: Printing the number of 3D keypoints generated
            print(f"Number of 3D keypoints(src, tar): {len(src_keypoints_3d), len(tar_keypoints_3d)}")
            keypoints = [len(src_keypoints_3d), len(tar_keypoints_3d)]

            # Assuming src_descriptors and tar_descriptors are your source and target descriptors
            good_matches = find_good_matches(src_pseudesc, tar_pseudesc)

            # Assuming good_matches contains your filtered matches
            matched_src_keypoints, matched_tar_keypoints, matched_src_descriptors, matched_tar_descriptors = \
                extract_matched_keypoints_descriptors(good_matches, src_keypoints_3d, tar_keypoints_3d, src_pseudesc, tar_pseudesc)

            # Applying RANSAC
            transformation = apply_ransac(matched_src_keypoints, matched_tar_keypoints, matched_src_descriptors, matched_tar_descriptors)
    
    # Check if the transformation was successful
    if transformation is not None:
        transformed_src = copy.deepcopy(src)
        transformed_src.transform(transformation)
        # print(transformation)  
        # o3d.visualization.draw_geometries([src, tar], width=800, height=600)
        # o3d.visualization.draw_geometries([transformed_src, tar], width=800, height=600)  
    else:
        print("Transformation failed.")
        print(transformation)
        return None, None, None, None, None, imdim, keypoints, if_col

    # Compute and print RMSE for quantitative evaluation
    init_rmse = compute_rmse(src, tar)
    rmse = compute_rmse(transformed_src, tar)

    # Compute color differences
    mean_color_init,mean_point_init  = compute_differences(src, tar)
    mean_color_regist, mean_point_regist = compute_differences(transformed_src, tar)
    
    return transformed_src, rmse, mean_color_regist, mean_point_regist, transformation, imdim, keypoints, if_col


Folder 'Arisa_NNSIFT' already exists.


# test

In [ ]:
fol = "D:/Users/msari/datasets/Wahington-Lai-rgbd/coffee_mug/coffee_mug_1"
source_point_cloud = o3d.io.read_point_cloud(f"{fol}/coffee_mug_1_2_4.ply")
target_point_cloud = o3d.io.read_point_cloud(f"{fol}/coffee_mug_1_2_20.ply")

print(f"source:{len(source_point_cloud.points)} points, target:{len(target_point_cloud.points)} points")

In [2]:
# Calculate bounding boxes of both point clouds
source_bbox = source_point_cloud.get_axis_aligned_bounding_box()
target_bbox = target_point_cloud.get_axis_aligned_bounding_box()

# Manually compute the diagonal length of bounding boxes
source_diagonal_length = np.linalg.norm(np.asarray(source_bbox.max_bound) - np.asarray(source_bbox.min_bound))
target_diagonal_length = np.linalg.norm(np.asarray(target_bbox.max_bound) - np.asarray(target_bbox.min_bound))

# Determine translation bounds
# Set the translation bounds as a fraction of the diagonal length of bounding boxes
translation_bound = max(source_diagonal_length, target_diagonal_length) * 0.1  # 10% of the maximum diagonal length

# Determine rotation bounds
# Here, we use a small fixed rotation bound (10 degrees converted to radians)
rotation_bound = np.radians(10)

randinit_source, randinit_transformation = random_initial_alignment(source_point_cloud, translation_bound, rotation_bound)
print(f"translation_bound:{translation_bound}, rotation_bound:{rotation_bound}")
print("random initial transformation:\n",randinit_transformation)

o3d.visualization.draw_geometries([source_point_cloud, target_point_cloud], width=800, height=600)
o3d.visualization.draw_geometries([randinit_source, target_point_cloud], width=800, height=600)

translation_bound:0.018911006860549497, rotation_bound:0.17453292519943295
random initial transformation:
 [[ 0.99854666 -0.04625112 -0.02766578  0.0184965 ]
 [ 0.04635645  0.99891991  0.00317787  0.00367637]
 [ 0.02748892 -0.00445574  0.99961218  0.0125031 ]
 [ 0.          0.          0.          1.        ]]


In [ ]:
src = copy.deepcopy(randinit_source)
tar = copy.deepcopy(target_point_cloud)
transformed_src, rmse, mean_color_regist, mean_point_regist, transformation, imdim =process_point_clouds(src, tar)

****
# Data looping(28102023)

In [ ]:
%run Mylib_import.ipynb
exp_dir = "Arisa_NNSIFT"
create_folder(exp_dir)

# Get all the folders
folders = glob.glob("D:/Users/msari/datasets/Wahington-Lai-rgbd/*/*")

# # Create a DataFrame to store the results
# results_df = pd.DataFrame(columns=['Source File', 'Target File', 'Image dim', 'RMSE', 'Mean Color Regist', 'Mean Point Regist', 'Transformation'])

for folder in folders: #for folder in folders[38/61-70/182-183/268/271](error):
    # Extracting the folder name
    folder_name = os.path.basename(folder)
    
    files = glob.glob(f"{folder}/*.ply")
    files.sort()  # Ensure files are processed in order
    
    # Create a DataFrame to store the results
    results_df = pd.DataFrame(columns=['Source File', 'Target File', 'Image dim', 'keypoints[src,tar]', 'RMSE', 'Mean Color Regist', 'Mean Point Regist', 'Transformation'])
    
    for i in range(0, len(files), 2):  # Pairing each file with the next one
        if i+1 < len(files):  # Check if there is a next file
            src_path = files[i]
            tar_path = files[i+1]
            
            src_ori = o3d.io.read_point_cloud(src_path)
            tar_ori = o3d.io.read_point_cloud(tar_path)
            src = copy.deepcopy(src_ori)
            tar = copy.deepcopy(tar_ori)
            transformed_src, rmse, mean_color_regist, mean_point_regist, transformation, imdim, keypoints = process_point_clouds(src, tar)

            # Extracting filenames without extension
            src_filename = os.path.splitext(os.path.basename(src_path))[0]
            tar_filename = os.path.splitext(os.path.basename(tar_path))[0]

            print(f"**Processed [{src_filename}] and [{tar_filename}]**")
            print(f"RMSE: {rmse}, Mean color regist: {mean_color_regist}, Mean point regist: {mean_point_regist}")
            # Append the results to the DataFrame
            results_df = results_df.append({
                'Source File': src_filename,
                'Target File': tar_filename,
                'Image dim': imdim,
                'keypoints[src,tar]': keypoints,
                'RMSE': rmse,
                'Mean Color Regist': mean_color_regist,
                'Mean Point Regist': mean_point_regist,
                'Transformation': np.array(transformation)
            }, ignore_index=True)

            # Save the DataFrame to an Excel file with the folder name
            results_df.to_excel(f'{exp_dir}/Wahington-Lai_results_{folder_name}.xlsx', index=False)

#         o3d.visualization.draw_geometries([src_ori, tar_ori], width=800, height=600)
#         o3d.visualization.draw_geometries([transformed_src, tar_ori], width=800, height=600)

****
# Data looping(30102023)

In [2]:
%run Mylib_import.ipynb
exp_dir = "Arisa_NNSIFT"
experiment_fol = 'test30102023'
create_folder(exp_dir)
create_folder(f'{exp_dir}/{experiment_fol}')
create_folder(f'{exp_dir}/{experiment_fol}/transformation')

# Get all the folders
folders = glob.glob("D:/Users/msari/datasets/Wahington-Lai-rgbd/*/*")

for folder in folders:
    # Extracting the folder name
    folder_name = os.path.basename(folder)
    create_folder(f'{exp_dir}/{experiment_fol}/transformation/{folder_name}')
    
    files = glob.glob(f"{folder}/*.ply")
    files.sort(key=sort_files_numerically)  # Sort files numerically
    
    # Create a DataFrame to store the results
    results_df = pd.DataFrame(columns=['Source File', 'Target File', 'Color', 'Image dim', 'keypoints[src,tar]', 'RMSE', 'Mean Color Regist', 'Mean Point Regist', 'Transformation'])
    
    # Processing each group of 10 files
    for i in range(0, len(files), 10):
        src_path = files[i]
        src_ori = o3d.io.read_point_cloud(src_path)
        
        # Targets are the next 9 files after the source
        for j in range(i+1, min(i+10, len(files))):
            tar_path = files[j]
            tar_ori = o3d.io.read_point_cloud(tar_path)
            src = copy.deepcopy(src_ori)
            tar = copy.deepcopy(tar_ori)
                
            transformed_src, rmse, mean_color_regist, mean_point_regist, transformation, imdim, keypoints, if_col = process_point_clouds(src, tar)

            # Extracting filenames without extension
            src_filename = os.path.splitext(os.path.basename(src_path))[0]
            tar_filename = os.path.splitext(os.path.basename(tar_path))[0]

            print(f"**Processed [{src_filename}] and [{tar_filename}]**")
            print(f"RMSE: {rmse}, Mean color regist: {mean_color_regist}, Mean point regist: {mean_point_regist}")

            # Append the results to the DataFrame
            results_df = results_df.append({
                'Source File': src_filename,
                'Target File': tar_filename,
                'Color': if_col,
                'Image dim': imdim,
                'keypoints[src,tar]': keypoints,
                'RMSE': rmse,
                'Mean Color Regist': mean_color_regist,
                'Mean Point Regist': mean_point_regist,
                'Transformation': np.array(transformation)
            }, ignore_index=True)

            # Check if transformation is not empty and is a 1D or 2D array
            if transformation is not None and isinstance(transformation, np.ndarray) and transformation.ndim in [1, 2]:
                # Save the numpy array to a text file
                np.savetxt(f"{exp_dir}/{experiment_fol}/transformation/{folder_name}/{src_filename}_{tar_filename}.txt", transformation, fmt="%s")
            else:
                # Save [['None']] to a text file
                with open(f"{exp_dir}/{experiment_fol}/transformation/{folder_name}/{src_filename}_{tar_filename}.txt", 'w') as file:
                    file.write("[['None']]")

            # Save the DataFrame to an Excel file with the folder name
            results_df.to_excel(f'{exp_dir}/{experiment_fol}/Wahington-Lai_results_{folder_name}.xlsx', index=False)

#         o3d.visualization.draw_geometries([src_ori, tar_ori], width=800, height=600)
#         o3d.visualization.draw_geometries([transformed_src, tar_ori], width=800, height=600)

Folder 'Arisa_NNSIFT' already exists.
Folder 'Arisa_NNSIFT/test30102023' already exists.
Folder 'Arisa_NNSIFT/test30102023/transformation' already exists.
Folder 'Arisa_NNSIFT/test30102023/transformation/stapler_1' created successfully.
----- Colored point clouds ------
Number of source keypoints extracted: (1, 8)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_1] and [stapler_1_1_2]**
RMSE: 0.001324838242692015, Mean color regist: 0.03446657233334624, Mean point regist: 0.0011633388269888883
----- Colored point clouds ------
Number of source keypoints extracted: (1, 5)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_1] and [stapler_1_1_3]**
RMSE: 0.0014573110685758045, Mean color regist: 0.03785660629538505, Mean point regist: 0.0012473203959987769
----- Colored point clouds ------
Number of source keypoints extracted: (1, 4)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_1] and [stapler_1_1_4]**
RMSE: 0.00149318

----- Colored point clouds ------
Number of source keypoints extracted: (2, 3)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_31] and [stapler_1_1_33]**
RMSE: 0.0016526305341126304, Mean color regist: 0.039887298339514037, Mean point regist: 0.001406711931536842
----- Colored point clouds ------
Number of source keypoints extracted: (2, 0)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_31] and [stapler_1_1_34]**
RMSE: 0.001681689409856601, Mean color regist: 0.03928900711807647, Mean point regist: 0.0014254754119787506
----- Colored point clouds ------
Number of source keypoints extracted: (2, 2)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_31] and [stapler_1_1_35]**
RMSE: 0.0018922603047652046, Mean color regist: 0.0449028435687882, Mean point regist: 0.0015614236472121957
----- Colored point clouds ------
Number of source keypoints extracted: (2, 0)
----- Keypoints are not proper detected ------
**Processed 

**Processed [stapler_1_1_61] and [stapler_1_1_65]**
RMSE: 0.0021456398341889544, Mean color regist: 0.06940194556665866, Mean point regist: 0.001744762093740966
----- Colored point clouds ------
Number of source keypoints extracted: (0, 1)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_61] and [stapler_1_1_66]**
RMSE: 0.0020388899899212655, Mean color regist: 0.058166728783084855, Mean point regist: 0.0017360925733415143
----- Colored point clouds ------
Number of source keypoints extracted: (0, 1)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_61] and [stapler_1_1_67]**
RMSE: 0.002811386911086514, Mean color regist: 0.09492783558255381, Mean point regist: 0.0023478138777305703
----- Colored point clouds ------
Number of source keypoints extracted: (0, 0)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_61] and [stapler_1_1_68]**
RMSE: 0.0030569389693172063, Mean color regist: 0.0794664599460388, Mean point regist

**Processed [stapler_1_1_91] and [stapler_1_1_97]**
RMSE: 0.0015852163292246083, Mean color regist: 0.0682713190093429, Mean point regist: 0.0013400469445386575
----- Colored point clouds ------
Number of source keypoints extracted: (1, 2)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_91] and [stapler_1_1_98]**
RMSE: 0.001860700267048541, Mean color regist: 0.06814394013271255, Mean point regist: 0.0015506551843191196
----- Colored point clouds ------
Number of source keypoints extracted: (1, 1)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_91] and [stapler_1_1_99]**
RMSE: 0.001752424486180945, Mean color regist: 0.06731312524726775, Mean point regist: 0.001451662291447129
----- Colored point clouds ------
Number of source keypoints extracted: (1, 4)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_91] and [stapler_1_1_100]**
RMSE: 0.001987342909205528, Mean color regist: 0.06017356181147422, Mean point regist: 

**Processed [stapler_1_1_121] and [stapler_1_1_129]**
RMSE: 0.003544099307188239, Mean color regist: 0.09223667230287991, Mean point regist: 0.002536466448502146
----- Colored point clouds ------
Number of source keypoints extracted: (3, 4)
Number of 3D keypoints(src, tar): (3, 4)
An error occurred: src_keypoints_3d is empty.
Transformation failed.
None
**Processed [stapler_1_1_121] and [stapler_1_1_130]**
RMSE: None, Mean color regist: None, Mean point regist: None
----- Colored point clouds ------
Number of source keypoints extracted: (0, 4)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_131] and [stapler_1_1_132]**
RMSE: 0.0010182564956243566, Mean color regist: 0.0376841722349994, Mean point regist: 0.0005605327357810021
----- Colored point clouds ------
Number of source keypoints extracted: (0, 0)
----- Keypoints are not proper detected ------
**Processed [stapler_1_1_131] and [stapler_1_1_133]**
RMSE: 0.0015303991678203156, Mean color regist: 0.0499508640

...

**Processed [water_bottle_9_4_121] and [water_bottle_9_4_128]**
RMSE: 0.006487036931927146, Mean color regist: 0.12270708145721293, Mean point regist: 0.004016034130593197
----- Colored point clouds ------
Number of source keypoints extracted: (10, 9)
Number of 3D keypoints(src, tar): (10, 9)
**Processed [water_bottle_9_4_121] and [water_bottle_9_4_129]**
RMSE: 0.02034276149247104, Mean color regist: 0.1822950278336759, Mean point regist: 0.018027193213049283
----- Colored point clouds ------
Number of source keypoints extracted: (10, 17)
Number of 3D keypoints(src, tar): (10, 17)
**Processed [water_bottle_9_4_121] and [water_bottle_9_4_130]**
RMSE: 0.004625516935589714, Mean color regist: 0.12478993742725132, Mean point regist: 0.0034059567479594152
----- Colored point clouds ------
Number of source keypoints extracted: (10, 11)
Number of 3D keypoints(src, tar): (10, 11)
**Processed [water_bottle_9_4_131] and [water_bottle_9_4_132]**
RMSE: 0.023908056755304736, Mean color regist: 0.22

**Processed [water_bottle_9_4_151] and [water_bottle_9_4_159]**
RMSE: 0.006072581762810719, Mean color regist: 0.1105773578778435, Mean point regist: 0.0042737739417854905
----- Colored point clouds ------
Number of source keypoints extracted: (13, 12)
Number of 3D keypoints(src, tar): (13, 12)
**Processed [water_bottle_9_4_151] and [water_bottle_9_4_160]**
RMSE: 0.0032118906276577958, Mean color regist: 0.08201043793119282, Mean point regist: 0.0026625793210731667
----- Colored point clouds ------
Number of source keypoints extracted: (12, 11)
Number of 3D keypoints(src, tar): (12, 11)
**Processed [water_bottle_9_4_161] and [water_bottle_9_4_162]**
RMSE: 0.005608956373219561, Mean color regist: 0.05616338955972623, Mean point regist: 0.002110496181544618
----- Colored point clouds ------
Number of source keypoints extracted: (12, 17)
Number of 3D keypoints(src, tar): (12, 17)
**Processed [water_bottle_9_4_161] and [water_bottle_9_4_163]**
RMSE: 0.00530890941254013, Mean color regist: 

----- Colored point clouds ------
Number of source keypoints extracted: (10, 7)
Number of 3D keypoints(src, tar): (10, 7)
**Processed [water_bottle_9_4_191] and [water_bottle_9_4_192]**
RMSE: 0.03045171157389584, Mean color regist: 0.2169503227022299, Mean point regist: 0.016993891953122096
----- Colored point clouds ------
Number of source keypoints extracted: (10, 8)
Number of 3D keypoints(src, tar): (10, 8)
**Processed [water_bottle_9_4_191] and [water_bottle_9_4_193]**
RMSE: 0.0028145563037117096, Mean color regist: 0.06427166962811828, Mean point regist: 0.0016340194640068447
----- Colored point clouds ------
Number of source keypoints extracted: (10, 12)
Number of 3D keypoints(src, tar): (10, 12)
**Processed [water_bottle_9_4_191] and [water_bottle_9_4_194]**
RMSE: 0.012367068324935044, Mean color regist: 0.2798993898560695, Mean point regist: 0.009843810740781252
----- Colored point clouds ------
Number of source keypoints extracted: (10, 4)
Number of 3D keypoints(src, tar): (10

----- Colored point clouds ------
Number of source keypoints extracted: (10, 8)
Number of 3D keypoints(src, tar): (10, 8)
**Processed [water_bottle_9_4_221] and [water_bottle_9_4_223]**
RMSE: 0.002624083188190102, Mean color regist: 0.06994502439590723, Mean point regist: 0.001929175127914065
----- Colored point clouds ------
Number of source keypoints extracted: (10, 5)
Number of 3D keypoints(src, tar): (10, 5)
**Processed [water_bottle_9_4_221] and [water_bottle_9_4_224]**
RMSE: 0.002754755778039098, Mean color regist: 0.057025261159986254, Mean point regist: 0.0015008170705434502
----- Colored point clouds ------
Number of source keypoints extracted: (10, 10)
Number of 3D keypoints(src, tar): (10, 10)
**Processed [water_bottle_9_4_221] and [water_bottle_9_4_225]**
RMSE: 0.0029447089250913524, Mean color regist: 0.10996128377623529, Mean point regist: 0.0022283659701733505
----- Colored point clouds ------
Number of source keypoints extracted: (10, 16)
Number of 3D keypoints(src, tar

**Processed [water_bottle_9_4_251] and [water_bottle_9_4_254]**
RMSE: 0.02462532830377473, Mean color regist: 0.285599244350734, Mean point regist: 0.019611468809570213
----- Colored point clouds ------
Number of source keypoints extracted: (9, 3)
Number of 3D keypoints(src, tar): (9, 3)
An error occurred: src_keypoints_3d is empty.
Transformation failed.
None
**Processed [water_bottle_9_4_251] and [water_bottle_9_4_255]**
RMSE: None, Mean color regist: None, Mean point regist: None
----- Colored point clouds ------
Number of source keypoints extracted: (9, 9)
Number of 3D keypoints(src, tar): (9, 9)
**Processed [water_bottle_9_4_251] and [water_bottle_9_4_256]**
RMSE: 0.03295180371674245, Mean color regist: 0.1959469201449714, Mean point regist: 0.02045093140959743
----- Colored point clouds ------
Number of source keypoints extracted: (9, 16)
Number of 3D keypoints(src, tar): (9, 16)
**Processed [water_bottle_9_4_251] and [water_bottle_9_4_257]**
RMSE: 0.0039657119678913715, Mean col

In [44]:
src_ = copy.deepcopy(src_ori)
tar_ = copy.deepcopy(tar_ori)
transrc_= copy.deepcopy(src_ori)
o3d.visualization.draw_geometries([src_, tar_], width=800, height=600)
transrc_.transform(transformation)
o3d.visualization.draw_geometries([transrc_, tar_], width=800, height=600)
transformation

****
# Import transformation

In [24]:
import pandas as pd
import numpy as np

%run Mylib_import.ipynb
exp_dir = "Arisa_NNSIFT"

# Specify the path to your Excel file
folder_name = 'cap_1' #'coffee_mug_1'
experiment_fol = 'test30102023'
excel_file_path = f'{exp_dir}/{experiment_fol}/Wahington-Lai_results_{folder_name}.xlsx'

# Load the Excel file into a DataFrame
df = pd.read_excel(excel_file_path)
all_T_arrays = []
all_src_name =[]
all_tar_name=[]
# Loop through each row in the DataFrame
for index, row in df.iterrows():
    # Get the transformation string
    transformation_str = row['Transformation']
    
    # Split the string into lines
    lines = transformation_str.splitlines()
    
    # Process each line
    transformation_array = []
    for line in lines:
        # Remove brackets and extra spaces
        line = line.replace("[", "").replace("]", "").strip()
        
        # Skip empty lines
        if line:
            # Split the line into elements
            elements = line.split()
            
            # Convert each element to a float if it's not 'None'
            float_elements = []
            for e in elements:
                try:
                    float_elements.append(float(e))
                except ValueError:
                    float_elements.append(None)  # or you can skip this element entirely
            
            transformation_array.append(float_elements)
            
    all_src_name.append(row['Source File'])
    all_tar_name.append(row['Target File'])
    all_T_arrays.append(transformation_array)
    # Convert the list of lists to a numpy array
    transformation_array = np.array(transformation_array)
    
#     # Save the numpy array to a text file
#     np.savetxt(f"{exp_dir}/{experiment_fol}/transformation/{folder_name}/{row['Source File']}_{row['Target File']}.txt", transformation_array, fmt="%s")
all_T_arrays

Folder 'Arisa_NNSIFT/test01/transformation' already exists.
Folder 'Arisa_NNSIFT/test01/transformation/coffee_mug_1' created successfully.


In [3]:
loop_n = 139
source_dir_test = f"D:/Users/msari/datasets/Wahington-Lai-rgbd/{folder_name[:-2]}/{folder_name}/{all_src_name[loop_n]}.ply"
target_dir_test = f"D:/Users/msari/datasets/Wahington-Lai-rgbd/{folder_name[:-2]}/{folder_name}/{all_tar_name[loop_n]}.ply"
print(f"source: {source_dir_test}, \ntarget: {target_dir_test}")
src_pcd = o3d.io.read_point_cloud(source_dir_test)
tar_pcd = o3d.io.read_point_cloud(target_dir_test)
all_T_arrays[loop_n]

'Arisa_NNSIFT/test01/Wahington-Lai_results_coffee_mug_1.xlsx'

In [21]:
src_ = copy.deepcopy(src_pcd)
tar_ = copy.deepcopy(tar_pcd)
transrc_= copy.deepcopy(src_pcd)
o3d.visualization.draw_geometries([src_, tar_], width=800, height=600)
transrc_.transform(all_T_arrays[loop_n])
o3d.visualization.draw_geometries([transrc_, tar_], width=800, height=600)

[[0.96846234, 0.19042662, -0.16068101, -0.11479182],
 [-0.17654925, 0.97952502, 0.09675281, 0.06830403],
 [0.17581538, -0.06533334, 0.98225277, -0.01173654],
 [0.0, 0.0, 0.0, 1.0]]

In [ ]:
all_src_name